## Search on Map

In [1]:
import lxml.etree as etree
import requests
import cioppy

import numpy as np
import ipyleaflet
from shapely.geometry import box
from shapely.geometry import multipolygon
from shapely.wkt import loads
from ipyleaflet import Map, Polygon

ciop = cioppy.Cioppy()

Define the Sentinel-1 endpoint

In [2]:
s1_osd_url = 'https://catalog.terradue.com/sentinel1/description'

Define an area of interest with a polygon over Greece expressed as a Well-Known Text:


In [3]:
aoi_wkt = 'POLYGON ((20.9113 39.4866, 20.9113 40.0866, 20.3113 40.0866, 20.3113 39.4866, 20.9113 39.4866))'

In [4]:
search_params = dict([('count', '2'),
                      ('geom', aoi_wkt)])

In [5]:
search = ciop.search(end_point=s1_osd_url,
                     params=search_params,
                     output_fields='self,productType,track,enclosure,identifier,wkt,startdate', 
                     model='EOP')

In [6]:
search

[{'enclosure': "https://scihub.copernicus.eu/apihub/odata/v1/Products('f05a7523-2fac-4179-9077-3608f3df007b')/$value",
  'identifier': 'S1B_IW_RAW__0SDV_20190506T163142_20190506T163214_016126_01E571_08A6',
  'productType': 'RAW',
  'self': 'https://catalog.terradue.com/sentinel1/search?format=atom&uid=S1B_IW_RAW__0SDV_20190506T163142_20190506T163214_016126_01E571_08A6',
  'startdate': '2019-05-06T16:31:42.4210000Z',
  'track': '175',
  'wkt': 'POLYGON((19.5985 39.4734,22.4468 39.7453,22.041 41.6995,19.1071 41.4254,19.5985 39.4734))'},
 {'enclosure': "https://scihub.copernicus.eu/apihub/odata/v1/Products('bfdf0851-eb0d-4515-b04e-675ae783c8a0')/$value",
  'identifier': 'S1B_IW_SLC__1SDV_20190506T163145_20190506T163212_016126_01E571_182A',
  'productType': 'SLC',
  'self': 'https://catalog.terradue.com/sentinel1/search?format=atom&uid=S1B_IW_SLC__1SDV_20190506T163145_20190506T163212_016126_01E571_182A',
  'startdate': '2019-05-06T16:31:45.3080000Z',
  'track': '175',
  'wkt': 'POLYGON((19

The search results provide the product footprint as a Well-Known Text (WKT) Polygon:

In [7]:
search[0]['wkt']

'POLYGON((19.5985 39.4734,22.4468 39.7453,22.041 41.6995,19.1071 41.4254,19.5985 39.4734))'

This WKT can be loaded and asked for the exterior coordinates as an array:

In [8]:
loads(search[0]['wkt']).exterior.coords[:]

[(19.5985, 39.4734),
 (22.4468, 39.7453),
 (22.041, 41.6995),
 (19.1071, 41.4254),
 (19.5985, 39.4734)]

ipyleaflet expects the coordinates in the lat, lon order. Numpy will swap the order of the values with:

In [9]:
np.asarray([t[::-1] for t in list(loads(search[0]['wkt']).exterior.coords)])

array([[ 39.4734,  19.5985],
       [ 39.7453,  22.4468],
       [ 41.6995,  22.041 ],
       [ 41.4254,  19.1071],
       [ 39.4734,  19.5985]])

In [10]:
np.asarray([t[::-1] for t in list(loads(search[0]['wkt']).exterior.coords)]).tolist()

[[39.4734, 19.5985],
 [39.7453, 22.4468],
 [41.6995, 22.041],
 [41.4254, 19.1071],
 [39.4734, 19.5985]]

Furthermore, ipyleaflet expects a list so the complete transformation of the WKT expression to ipyleaflet is:

In [11]:
search_locations = np.asarray([t[::-1] for t in list(loads(search[0]['wkt']).exterior.coords)]).tolist()

Let's apply the same for our AOI:

In [12]:
aoi_locations = np.asarray([t[::-1] for t in list(loads(aoi_wkt).exterior.coords)]).tolist()

The map will be centered on the AOI centroid:

In [13]:
map_center_x = loads(aoi_wkt).centroid.x
map_center_y = loads(aoi_wkt).centroid.y

Now we'll create the map:

In [14]:
m = Map(center=(loads(aoi_wkt).centroid.y, 
                loads(aoi_wkt).centroid.x), 
                zoom=6)

for index, elem in enumerate(search):

    search_locations = np.asarray([t[::-1] for t in list(loads(elem['wkt']).exterior.coords)]).tolist()
    
    m += Polygon(locations=search_locations,
                 color="red",
                 fill_color="red",
                 weight=1,
                 fill_opacity=0.1)

m += Polygon(locations=aoi_locations,
             color="green",
             fill_color="green",
             weight=1,
             fill_opacity=0.1)
m

TWFwKGJhc2VtYXA9eyd1cmwnOiAnaHR0cHM6Ly97c30udGlsZS5vcGVuc3RyZWV0bWFwLm9yZy97en0ve3h9L3t5fS5wbmcnLCAnbWF4X3pvb20nOiAxOSwgJ2F0dHJpYnV0aW9uJzogJ01hcCDigKY=
